<a href="https://colab.research.google.com/github/szucshey/osm-data-exploration/blob/main/szakdolgozat.ipynb" target="_parent"><img src="https://colab.research.google.com/assets/colab-badge.svg" alt="Open In Colab"/></a>

In [ ]:
#szükséges könyvtárak telepítése

pip install geopandas overpy overpass geojson

     |████████████████████████████████| 1.0 MB 14.1 MB/s 
     |████████████████████████████████| 47 kB 4.5 MB/s 
     |████████████████████████████████| 16.7 MB 41.8 MB/s 
     |████████████████████████████████| 6.3 MB 44.6 MB/s 
  Created wheel for overpy: filename=overpy-0.6-py3-none-any.whl size=14106 sha256=812d070dc28db700cb5a8be33e0e0951ed3816e51b17539addb0aaf67cfeb241
  Stored in directory: /root/.cache/pip/wheels/1a/d3/0e/090c6914956cc37881fc914101d2a952c0da8e66fc86dc6a31
Successfully built overpy


In [ ]:
import overpy
import requests
import json
import geojson
#Magyarország megyehatárainak lekérése az OSM API-n keresztül
overpass_url = "http://overpass-api.de/api/interpreter"
overpass_query = """
    [out:json];
    rel["ISO3166-2"~"^HU"]
    [admin_level=6]
    [type=boundary]
    [boundary=administrative];
    out geom;
    """
response = requests.get(overpass_url, params={'data': overpass_query})
data = response.json()

In [322]:
import folium

m = folium.Map([47.611, 19.505], zoom_start=8, min_zoom=8, max_zoom=8, tiles='https://server.arcgisonline.com/ArcGIS/rest/services/Canvas/World_Light_Gray_Base/MapServer/tile/{z}/{y}/{x}', attr="Attribútum")

data=r"/content/geojson.json"

g = folium.GeoJson(data, name='geojson').add_to(m)

folium.GeoJsonTooltip(fields=["name"]).add_to(g)

m

In [327]:
import pandas as pd

df = pd.read_csv(f"/content/covid-megyei-mind.csv", delimiter=";")
#--------------------------------------------------------------------
#szűrendő dátum megadása YYYY.MM.DD formátumban
date_filter = "2021.09.07"
#--------------------------------------------------------------------

choropleth_table = df[df["Dátum"] == date_filter]
choropleth_table = choropleth_table[['Megye', 'Fertőzöttek']]

m = folium.Map([47.611, 19.505], zoom_start=8, min_zoom=8, max_zoom=8, tiles='https://server.arcgisonline.com/ArcGIS/rest/services/Canvas/World_Light_Gray_Base/MapServer/tile/{z}/{y}/{x}', attr="Attribútum")

c = folium.Choropleth(
    geo_data=data,
    name="choropleth",
    data=choropleth_table,
    columns=["Megye", "Fertőzöttek"],
    key_on='feature.properties.name',
    fill_color='YlOrRd',
    bins=[choropleth_table['Fertőzöttek'].min(),
          1*(choropleth_table['Fertőzöttek'].max() - choropleth_table['Fertőzöttek'].min()) / 7 + choropleth_table['Fertőzöttek'].min(), 
          2*(choropleth_table['Fertőzöttek'].max() - choropleth_table['Fertőzöttek'].min()) / 7 + choropleth_table['Fertőzöttek'].min(),
          3*(choropleth_table['Fertőzöttek'].max() - choropleth_table['Fertőzöttek'].min()) / 7 + choropleth_table['Fertőzöttek'].min(), 
          4*(choropleth_table['Fertőzöttek'].max() - choropleth_table['Fertőzöttek'].min()) / 7 + choropleth_table['Fertőzöttek'].min(), 
          5*(choropleth_table['Fertőzöttek'].max() - choropleth_table['Fertőzöttek'].min()) / 7 + choropleth_table['Fertőzöttek'].min(), 
          6*(choropleth_table['Fertőzöttek'].max() - choropleth_table['Fertőzöttek'].min()) / 7 + choropleth_table['Fertőzöttek'].min(), 
          choropleth_table['Fertőzöttek'].max()],
    highlight=True,
    fill_opacity=1,
    line_opacity=1,
    legend_name="Fertőzöttek száma megyékre bontva - " + date_filter
)
c.add_to(m)

tooltip = []
for idx in range(choropleth_table.index[len(choropleth_table)-1]-19, choropleth_table.index[len(choropleth_table)-1]+1):
  tooltip.append(idx)

with open('/content/geojson.json') as f:
    data = json.load(f)

for idx in range(len(tooltip)):
    data['features'][idx]['properties']['tooltip'] = data['features'][idx]['properties']['name'] + ": " + str(int(choropleth_table[choropleth_table["Megye"] == data['features'][idx]['properties']['name']]['Fertőzöttek']))

folium.LayerControl().add_to(m)
c.geojson.add_child(
    folium.features.GeoJsonTooltip(['tooltip'], labels=False)
)

m